# 00 – Environment & Setup - Run only once

In [ ]:
# src/bootstrap.py
from __future__ import annotations
import re, json, os
from pathlib import Path
import yaml

def find_project_root(max_up: int = 8) -> Path:
    p = Path.cwd()
    for _ in range(max_up):
        if (p / "configs").exists() and ((p / "src").exists() or (p / "notebooks").exists()):
            return p
        p = p.parent
    # If nothing matches, assume CWD is the root and create minimal scaffold
    root = Path.cwd()
    (root / "configs").mkdir(parents=True, exist_ok=True)
    (root / "src").mkdir(parents=True, exist_ok=True)
    (root / "notebooks").mkdir(parents=True, exist_ok=True)
    return root

def _slugify(s: str) -> str:
    return re.sub(r"[^0-9a-zA-Z]+", "-", (s or "").strip().lower()).strip("-") or "unknown"

def ensure_run_yaml(root: Path) -> Path:
    """Create configs/run.yaml only if missing; never overwrite."""
    cfg_dir = root / "configs"
    cfg_dir.mkdir(parents=True, exist_ok=True)
    run_yaml = cfg_dir / "run.yaml"
    if not run_yaml.exists():
        run_yaml.write_text(
            yaml.safe_dump({
                "current_state": "",          # populated by Notebook 01 at runtime
                "current_issue": "",          # populated by Notebook 01 at runtime
                "paths": {
                    "data":    "data/{state}",
                    "outputs": "outputs/{state}",
                    "logs":    "logs/{state}"
                }
            }, sort_keys=False),
            encoding="utf-8"
        )
    return run_yaml

def load_run_cfg(root: Path) -> dict:
    run_yaml = ensure_run_yaml(root)
    try:
        return yaml.safe_load(run_yaml.read_text(encoding="utf-8")) or {}
    except Exception:
        return {}

def resolve_outputs_dir(root: Path, state_name: str | None) -> Path:
    """Prefer <slug>-state, else <slug>. Does not invent a fallback state."""
    if not state_name:
        raise ValueError("No state set. Update configs/run.yaml via Notebook 01.")
    slug = _slugify(state_name)
    cand1 = root / "outputs" / f"{slug}-state"
    cand2 = root / "outputs" / slug
    if cand1.exists():
        return cand1
    if cand2.exists():
        return cand2
    # if neither exists, create the preferred `<slug>-state`
    cand1.mkdir(parents=True, exist_ok=True)
    return cand1

def get_current_context(root: Path) -> dict:
    """
    Returns {'state': str|'', 'issue': str|'' , 'outputs_dir': Path}
    Does not inject defaults; relies on run.yaml being set by Notebook 01.
    """
    cfg = load_run_cfg(root)
    state = (cfg.get("current_state") or "").strip()
    issue = (cfg.get("current_issue") or "").strip()
    out_dir = resolve_outputs_dir(root, state) if state else None
    return {"state": state, "issue": issue, "outputs_dir": out_dir}